In [ ]:
!pip install kaggle

In [ ]:
from google.colab import files
files.upload()

Saving kaggle.json to kaggle.json


{'kaggle.json': b'{"username":"ark610475","key":"623eb513c4d4ecd0fc247622e5713f33"}'}

In [ ]:
!mkdir -p ~/.kaggle
!mv kaggle.json ~/.kaggle/
!chmod 600 ~/.kaggle/kaggle.json

In [ ]:
!kaggle competitions download -c dm-2024-isa-5810-lab-2-homework

100% 149M/149M [00:01<00:00, 140MB/s] 
100% 149M/149M [00:01<00:00, 103MB/s]


In [ ]:
!unzip dm-2024-isa-5810-lab-2-homework.zip

Archive:  dm-2024-isa-5810-lab-2-homework.zip
  inflating: data_identification.csv  
  inflating: emotion.csv             
  inflating: sampleSubmission.csv    
  inflating: tweets_DM.json          


In [ ]:
import json
import pandas as pd
import numpy as np
import torch
from torch.utils.data import Dataset, DataLoader
from transformers import BertTokenizer, BertForSequenceClassification, get_scheduler
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import f1_score
from sklearn.utils.class_weight import compute_class_weight
from torch.amp import autocast, GradScaler
import torch.multiprocessing as mp

emotion = pd.read_csv('/content/emotion.csv')
data_identification = pd.read_csv('/content/data_identification.csv')

with open('/content/tweets_DM.json', 'r') as f:
  data = [json.loads(line) for line in f]

  df = pd.DataFrame(data)
  _source = df['_source'].apply(lambda x: x['tweet'])
  df = pd.DataFrame({
        'tweet_id': _source.apply(lambda x: x['tweet_id']),
        'hashtags': _source.apply(lambda x: x['hashtags']),
        'text': _source.apply(lambda x: x['text']),
    })
  df = df.merge(data_identification, on='tweet_id', how='left')

  train_data = df[df['identification'] == 'train']
  test_data = df[df['identification'] == 'test']

  train_data = train_data.merge(emotion, on='tweet_id', how='left')
  train_data.drop_duplicates(subset=['text'], keep=False, inplace=True)


In [ ]:
print(len(test_data))

411972


In [ ]:
emo_to_id = {
    'anger' : 0,
    'anticipation' : 1,
    'disgust' : 2,
    'fear' : 3,
    'sadness' : 4,
    'surprise' : 5,
    'trust' : 6,
    'joy' : 7
}
id_to_emo ={
    0 : 'anger',
    1 : 'anticipation',
    2 : 'disgust',
    3 : 'fear',
    4 : 'sadness',
    5 : 'surprise',
    6 : 'trust',
    7 : 'joy'
}

train_data['emo_id'] = train_data['emotion'].apply(lambda x: emo_to_id[x])

In [ ]:
!pip install datasets==2.21.0

INFO: pip is looking at multiple versions of multiprocess to determine which version is compatible with other requirements. This could take a while.
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 527.3/527.3 kB 13.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 11.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 177.6/177.6 kB 16.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 12.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 17.9 MB/s eta 0:00:00
  Attempting uninstall: fsspec
    Found existing installation: fsspec 2024.10.0
    Uninstalling fsspec-2024.10.0:
      Successfully uninstalled fsspec-2024.10.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
gcsfs 2024.10.0 requires fsspec==2024.10.0, but you have fsspec 2024.6.1 which is incompatible.


In [ ]:
!pip install torchmetrics

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 926.4/926.4 kB 18.6 MB/s eta 0:00:00


In [ ]:
!pip install transformers

In [ ]:
import transformers as T
import datasets
from datasets import load_dataset
import torch
from torch.utils.data import Dataset, DataLoader
from torch.optim import AdamW
from tqdm import tqdm
from torchmetrics import SpearmanCorrCoef, Accuracy, F1Score
from transformers import BertModel,BertTokenizer
from sklearn.ensemble import VotingRegressor
device = "cuda:0" if torch.cuda.is_available() else "cpu"

In [ ]:
class Dataset(torch.utils.data.Dataset):
    def __init__(self, sequences):
        self.sequences = sequences

    def __len__(self):
        return len(self.sequences)

    def __getitem__(self, index):
        x = self.sequences.iloc[index][0]
        y = self.sequences.iloc[index][1]

        return x, y
class TestDataset(torch.utils.data.Dataset):
    def __init__(self, sequences):
        self.sequences = sequences

    def __len__(self):
        return len(self.sequences)

    def __getitem__(self, index):
        x = self.sequences.iloc[index]
        return x

In [ ]:
def collate_fn(batch):
    text = [data[0] for data in batch]

    text = tokenizer(text,padding = True,truncation = True,return_tensors = "pt")
    emo = torch.tensor([data[1] for data in batch],dtype = torch.long)

    return text, emo

def collate_fn_test(batch):
    text = [data for data in batch]

    text = tokenizer(text,padding = True,truncation = True,return_tensors = "pt")

    return text


In [ ]:
train_data_sample = train_data.sample(frac = 0.2)
train_data_sample, test_data_sample = train_test_split(train_data_sample, test_size=0.5, random_state=42)

In [ ]:
ds_train = Dataset(train_data_sample[['text', 'emo_id']])
ds_test = Dataset(train_data_sample[['text', 'emo_id']])
ds_real_test = TestDataset(test_data['text'])

In [ ]:
class MultiLabelModel(torch.nn.Module):
    def __init__(self, *args, **kwargs):
        super().__init__(*args, **kwargs)
        self.bert = BertModel.from_pretrained("bert-base-uncased")

        self.classification = torch.nn.Linear(self.bert.config.hidden_size, 8)

        self.softmax = torch.nn.Softmax(dim=1)

    def forward(self, **kwargs):
        input_ids = kwargs.get('input_ids')
        attention_mask = kwargs.get('attention_mask')

        outputs = self.bert(input_ids=input_ids, attention_mask=attention_mask)

        x = outputs.pooler_output

        emo = self.classification(x)
        emo = self.softmax(emo)

        return emo



In [ ]:
dl_train = DataLoader(dataset = ds_train, batch_size = 64, shuffle = True, collate_fn = collate_fn)
dl_test = DataLoader(dataset = ds_test, batch_size = 64, shuffle = False, collate_fn = collate_fn)
dl_real_test = DataLoader(dataset=ds_real_test, batch_size=64, shuffle=False, collate_fn=collate_fn_test)

In [ ]:
model = MultiLabelModel().to(device)
tokenizer = T.BertTokenizer.from_pretrained("google-bert/bert-base-uncased", cache_dir="./cache/")

In [ ]:
epochs = 2
optimizer = torch.optim.Adam(model.parameters(), lr=2e-5, eps=1e-8)
classification_loss_fn = torch.nn.CrossEntropyLoss()

In [ ]:
from torchmetrics import Accuracy, F1Score

accuracy = Accuracy(task="multiclass",num_classes=8).to(device)
f1_score = F1Score(task="multiclass",average="macro", num_classes=8).to(device)

In [ ]:
for ep in range(epochs):
    pbar = tqdm(dl_train)
    pbar.set_description(f"Training epoch [{ep+1}/{epochs}]")
    model.train()
    for text,emotion in pbar:
        optimizer.zero_grad()

        input_ids = text['input_ids'].to(device)
        attention_mask = text['attention_mask'].to(device)
        emo = emotion.to(device)

        emo_pred = model(input_ids=input_ids, attention_mask=attention_mask)

        loss = classification_loss_fn(emo_pred, emo)
        loss.backward()

        optimizer.step()

Training epoch [1/1]:   0%|          | 0/2265 [00:00<?, ?it/s]<ipython-input-16-b649a17b9bd4>:9: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  x = self.sequences.iloc[index][0]
<ipython-input-16-b649a17b9bd4>:10: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  y = self.sequences.iloc[index][1]
Training epoch [1/1]: 100%|██████████| 2265/2265 [19:48<00:00,  1.91it/s]


In [ ]:
 for ep in range(epochs):
    pbar = tqdm(dl_test)
    pbar.set_description(f"Validation epoch [{ep+1}/{epochs}]")
    model.eval()
    with torch.no_grad():
      for text,emotion in pbar:

        input_ids = text['input_ids'].to(device)
        attention_mask = text['attention_mask'].to(device)
        emo = emotion.to(device)

        emo_pred = model(input_ids=input_ids, attention_mask=attention_mask)

        loss = classification_loss_fn(emo_pred, emo)

        accuracy.update(emo_pred, emo)
        f1_score.update(emo_pred, emo)


Validation epoch [1/1]:   0%|          | 0/2265 [00:00<?, ?it/s]<ipython-input-16-b649a17b9bd4>:9: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  x = self.sequences.iloc[index][0]
<ipython-input-16-b649a17b9bd4>:10: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  y = self.sequences.iloc[index][1]
Validation epoch [1/1]: 100%|██████████| 2265/2265 [08:03<00:00,  4.68it/s]


In [ ]:
accuracy_score = accuracy.compute()
f1_score_val = f1_score.compute()
print(f"Accuracy: {accuracy_score:.4f}")
print(f"F1 Score: {f1_score_val:.4f}")

accuracy.reset()
f1_score.reset()

Accuracy: 0.5021
F1 Score: 0.2638


In [ ]:
predictions = []

model.eval()
pbar = tqdm(dl_real_test)
with torch.no_grad():
    for text in pbar:
        input_ids = text['input_ids'].to(device)
        attention_mask = text['attention_mask'].to(device)


        emo_pred = model(input_ids=input_ids, attention_mask=attention_mask)

        predicted_emotion = torch.argmax(emo_pred, dim=1).tolist()
        predictions.extend([id_to_emo[x] for x in predicted_emotion])

print(predictions)

100%|██████████| 6438/6438 [20:34<00:00,  5.22it/s]

['sadness', 'trust', 'anticipation', 'joy', 'joy', 'sadness', 'joy', 'joy', 'joy', 'anticipation', 'trust', 'disgust', 'disgust', 'joy', 'joy', 'trust', 'joy', 'anticipation', 'sadness', 'anticipation', 'surprise', 'trust', 'sadness', 'sadness', 'anticipation', 'anticipation', 'trust', 'joy', 'sadness', 'joy', 'anger', 'trust', 'sadness', 'joy', 'anticipation', 'disgust', 'trust', 'anticipation', 'trust', 'trust', 'trust', 'joy', 'sadness', 'joy', 'trust', 'joy', 'sadness', 'trust', 'joy', 'joy', 'fear', 'joy', 'trust', 'sadness', 'anticipation', 'joy', 'joy', 'joy', 'anger', 'joy', 'trust', 'sadness', 'joy', 'joy', 'sadness', 'trust', 'anticipation', 'joy', 'joy', 'sadness', 'joy', 'joy', 'joy', 'anticipation', 'trust', 'disgust', 'disgust', 'joy', 'joy', 'trust', 'joy', 'anticipation', 'sadness', 'anticipation', 'surprise', 'trust', 'sadness', 'sadness', 'anticipation', 'anticipation', 'trust', 'joy', 'sadness', 'joy', 'anger', 'trust', 'sadness', 'joy', 'anticipation', 'disgust', 't

In [ ]:
print(len(predictions))

412032


In [ ]:
submission = pd.DataFrame({
    'id': test_data['tweet_id'],
    'emotion': predictions[:len(test_data)]
})

In [ ]:
submission.head()

id       emotion
2   0x28b412       sadness
4   0x2de201         trust
9   0x218443  anticipation
30  0x2939d5           joy
33  0x26289a           joy

In [ ]:
pbar = tqdm(dl_test)
with torch.no_grad():
    for i,(text,emotion) in enumerate(pbar):

      input_ids = text['input_ids'].to(device)
      attention_mask = text['attention_mask'].to(device)
      emo = emotion.to(device)

      original_emotion = emo.view(-1).tolist()

      emo_pred = model(input_ids=input_ids, attention_mask=attention_mask)

      predicted_emotion = torch.argmax(emo_pred, dim=1).tolist()

      print("Batch:",i)
      print("Original emotion:",[id_to_emo[x] for x in original_emotion])
      print("Predicted emotion:",[id_to_emo[x] for x in predicted_emotion])
      print("\n")

  0%|          | 0/2265 [00:00<?, ?it/s]<ipython-input-16-b649a17b9bd4>:9: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  x = self.sequences.iloc[index][0]
<ipython-input-16-b649a17b9bd4>:10: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  y = self.sequences.iloc[index][1]
  0%|          | 1/2265 [00:00<11:31,  3.28it/s]

Batch: 0
Original emotion: ['anger', 'disgust', 'joy', 'joy', 'joy', 'sadness', 'joy', 'joy', 'trust', 'joy', 'joy', 'joy', 'sadness', 'sadness', 'joy', 'joy', 'disgust', 'anticipation', 'joy', 'anticipation', 'anticipation', 'joy', 'trust', 'sadness', 'surprise', 'sadness', 'joy', 'disgust', 'disgust', 'disgust', 'trust', 'sadness', 'trust', 'disgust', 'joy', 'disgust', 'disgust', 'anticipation', 'trust', 'sadness', 'anticipation', 'disgust', 'joy', 'sadness', 'trust', 'joy', 'joy', 'sadness', 'sadness', 'sadness', 'trust', 'disgust', 'anticipation', 'trust', 'joy', 'anticipation', 'trust', 'disgust', 'trust', 'surprise', 'fear', 'joy', 'disgust', 'joy']
Predicted emotion: ['sadness', 'sadness', 'sadness', 'joy', 'sadness', 'sadness', 'joy', 'joy', 'joy', 'joy', 'joy', 'disgust', 'disgust', 'sadness', 'joy', 'joy', 'joy', 'anticipation', 'joy', 'anticipation', 'joy', 'anticipation', 'joy', 'sadness', 'joy', 'sadness', 'joy', 'joy', 'disgust', 'sadness', 'anticipation', 'sadness', 'ant

  0%|          | 2/2265 [00:00<09:46,  3.86it/s]

Batch: 1
Original emotion: ['joy', 'joy', 'sadness', 'anticipation', 'anticipation', 'joy', 'surprise', 'trust', 'trust', 'joy', 'joy', 'joy', 'anticipation', 'joy', 'sadness', 'sadness', 'surprise', 'joy', 'anticipation', 'sadness', 'joy', 'joy', 'sadness', 'anticipation', 'joy', 'fear', 'joy', 'joy', 'anticipation', 'sadness', 'trust', 'anticipation', 'trust', 'disgust', 'joy', 'trust', 'joy', 'joy', 'sadness', 'fear', 'sadness', 'joy', 'sadness', 'disgust', 'anticipation', 'disgust', 'trust', 'joy', 'fear', 'anticipation', 'anticipation', 'trust', 'surprise', 'anticipation', 'joy', 'trust', 'anticipation', 'surprise', 'fear', 'joy', 'disgust', 'anger', 'joy', 'joy']
Predicted emotion: ['anticipation', 'anticipation', 'sadness', 'anticipation', 'anticipation', 'joy', 'sadness', 'joy', 'anticipation', 'joy', 'joy', 'joy', 'joy', 'joy', 'sadness', 'joy', 'anticipation', 'anticipation', 'joy', 'sadness', 'sadness', 'joy', 'disgust', 'anticipation', 'joy', 'joy', 'joy', 'joy', 'joy', 'sa

  0%|          | 3/2265 [00:00<09:18,  4.05it/s]

...

Batch: 201
Original emotion: ['joy', 'joy', 'joy', 'anticipation', 'anticipation', 'trust', 'joy', 'sadness', 'sadness', 'sadness', 'sadness', 'trust', 'anticipation', 'trust', 'fear', 'trust', 'joy', 'trust', 'joy', 'sadness', 'joy', 'sadness', 'surprise', 'sadness', 'joy', 'trust', 'trust', 'anticipation', 'anticipation', 'joy', 'trust', 'anger', 'joy', 'joy', 'trust', 'joy', 'anticipation', 'anticipation', 'sadness', 'trust', 'anticipation', 'joy', 'joy', 'sadness', 'fear', 'trust', 'joy', 'joy', 'joy', 'sadness', 'joy', 'sadness', 'joy', 'joy', 'joy', 'disgust', 'sadness', 'joy', 'sadness', 'anticipation', 'joy', 'joy', 'anticipation', 'sadness']
Predicted emotion: ['joy', 'joy', 'joy', 'anticipation', 'anticipation', 'joy', 'joy', 'sadness', 'joy', 'sadness', 'sadness', 'anticipation', 'anticipation', 'sadness', 'anticipation', 'joy', 'joy', 'joy', 'joy', 'anticipation', 'joy', 'disgust', 'sadness', 'sadness', 'joy', 'joy', 'joy', 'joy', 'anticipation', 'joy', 'joy', 'joy', 'joy',

  9%|▉         | 203/2265 [00:46<07:28,  4.60it/s]

Batch: 202
Original emotion: ['joy', 'joy', 'trust', 'joy', 'sadness', 'anticipation', 'joy', 'joy', 'trust', 'trust', 'joy', 'anger', 'anticipation', 'sadness', 'disgust', 'fear', 'trust', 'trust', 'sadness', 'disgust', 'anticipation', 'anticipation', 'joy', 'sadness', 'joy', 'joy', 'anticipation', 'joy', 'fear', 'joy', 'disgust', 'anger', 'anticipation', 'sadness', 'anticipation', 'anticipation', 'joy', 'joy', 'fear', 'joy', 'trust', 'anticipation', 'joy', 'joy', 'joy', 'anticipation', 'disgust', 'joy', 'sadness', 'sadness', 'surprise', 'anticipation', 'trust', 'joy', 'disgust', 'anticipation', 'joy', 'anticipation', 'joy', 'fear', 'disgust', 'disgust', 'sadness', 'joy']
Predicted emotion: ['anticipation', 'joy', 'joy', 'sadness', 'sadness', 'joy', 'disgust', 'joy', 'anticipation', 'anticipation', 'disgust', 'sadness', 'anticipation', 'joy', 'disgust', 'anticipation', 'joy', 'joy', 'sadness', 'disgust', 'anticipation', 'joy', 'sadness', 'sadness', 'joy', 'joy', 'anticipation', 'joy',

  9%|▉         | 203/2265 [00:46<07:49,  4.39it/s]


KeyboardInterrupt: 

In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.naive_bayes import ComplementNB
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import classification_report, accuracy_score, confusion_matrix
from sklearn.model_selection import GridSearchCV
import nltk
nltk.download('punkt_tab')



vectorizer = TfidfVectorizer(max_features=1000,tokenizer=nltk.word_tokenize)
tfidf_train = vectorizer.fit_transform(train_data_sample['text'])

[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt_tab.zip.
/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:521: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


In [ ]:
tfidf_test = vectorizer.fit_transform(test_data_sample['text'])

/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:521: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


In [ ]:
tfidf_feature_names_1000 = vectorizer.get_feature_names_out()
tfidf_feature_names_1000[100:110]

In [ ]:
X_train = tfidf_train
y_train = train_data_sample['emotion']

X_test = tfidf_test
y_test = test_data_sample['emotion']

cp_model = ComplementNB()
cp_model = cp_model.fit(X_train,y_train)

y_cp_train_pred = cp_model.predict(X_train)
y_cp_test_pred = cp_model.predict(X_test)

y_cp_test_pred[:10]


array(['sadness', 'joy', 'sadness', 'disgust', 'anticipation', 'trust',
       'joy', 'joy', 'anticipation', 'joy'], dtype='<U12')

In [ ]:
from sklearn.metrics import accuracy_score
from sklearn.metrics import classification_report

In [ ]:
acc_train = accuracy_score(y_true=y_train, y_pred=y_cp_train_pred)
acc_test = accuracy_score(y_true=y_test, y_pred=y_cp_test_pred)

print('training accuracy: {}'.format(round(acc_train, 2)))
print('testing accuracy: {}'.format(round(acc_test, 2)))

print(classification_report(y_true=y_test, y_pred=y_cp_test_pred))
cm = confusion_matrix(y_true=y_test, y_pred=y_cp_test_pred)
print(cm)


training accuracy: 0.43
testing accuracy: 0.26
              precision    recall  f1-score   support

       anger       0.33      0.08      0.13      4022
anticipation       0.26      0.30      0.28     24553
     disgust       0.17      0.20      0.18     13853
        fear       0.05      0.17      0.08      6350
         joy       0.46      0.37      0.41     51489
     sadness       0.21      0.18      0.20     19274
    surprise       0.06      0.02      0.03      4767
       trust       0.20      0.19      0.20     20611

    accuracy                           0.26    144919
   macro avg       0.22      0.19      0.19    144919
weighted avg       0.29      0.26      0.27    144919

[[  324   694   579   606   817   445    29   528]
 [   95  7251  2201  3970  5800  1975   311  2950]
 [   72  2185  2812  2022  2600  2133   147  1882]
 [   25  1060   958  1058  1616   809    65   759]
 [  213  9097  4452  6331 19189  5119   541  6547]
 [  122  3220  3004  2950  3813  3516   170  24

In [ ]:
y_test_pred = model.predict(X_test_data)